In [0]:
from pyspark.sql.functions import *
from pyspark.sql.window import Window

In [0]:
charges_df=spark.read.format("csv").option("header","true").option("inferSchema","true").load("/mnt/mountdatalake/aparna/Charges_use.csv")
charges_df=charges_df.dropDuplicates()
# display(charges_df)

In [0]:
damage_df=spark.read.format("csv").option("header","true").option("inferSchema","true").load("/mnt/mountdatalake/aparna/Damages_use.csv")
damage_df=damage_df.dropDuplicates()
# display(damage_df)

In [0]:
endorse_df=spark.read.format("csv").option("header","true").option("inferSchema","true").load("/mnt/mountdatalake/aparna/Endorse_use.csv")
endorse_df=endorse_df.dropDuplicates()
# display(endorse_df)

In [0]:
person_df=spark.read.format("csv").option("header","true").option("inferSchema","true").load("/mnt/mountdatalake/aparna/Primary_Person_use.csv")
person_df=person_df.dropDuplicates()
# display(person_df)

In [0]:
restrict_df=spark.read.format("csv").option("header","true").option("inferSchema","true").load("/mnt/mountdatalake/aparna/Restrict_use.csv")
restrict_df=person_df.dropDuplicates()
# # display(restrict_df)

In [0]:
units_df=spark.read.format("csv").option("header","true").option("inferSchema","true").load("/mnt/mountdatalake/aparna/Units_use.csv")
units_df=units_df.dropDuplicates()

# display(units_df)

In [0]:
question1 = person_df.filter((col('PRSN_GNDR_ID') =='MALE') & (col('DEATH_CNT')>0)).groupBy('CRASH_ID').count()\
            .filter("count>2")
result1 = spark.createDataFrame([(question1.count())], "integer").toDF("NO_OF_MALE_KILLED_CRASH")
display(result1)

NO_OF_MALE_KILLED_CRASH 0

In [0]:
question2 = units_df.filter(col('VEH_BODY_STYL_ID').contains('MOTORCYCLE')).count()
print(question2)


773


In [0]:
question3 = person_df.filter((col('DEATH_CNT')>0) & (col('PRSN_AIRBAG_ID')=='NOT DEPLOYED'))\
            .join(units_df,on=['CRASH_ID','UNIT_NBR'],how="Inner")\
            .groupBy('VEH_MAKE_ID').count()\
            .orderBy(col('count').desc())\
            .limit(5)\
            .select('VEH_MAKE_ID')
display(question3)
print([row[0] for row in question3.collect()])

VEH_MAKE_ID CHEVROLET FORD NISSAN HONDA DODGE

['CHEVROLET', 'FORD', 'NISSAN', 'HONDA', 'DODGE']


In [0]:
question4 = units_df.filter(col('VEH_HNR_FL')=='Y')\
            .join(person_df,on=['CRASH_ID','UNIT_NBR'],how="inner")\
            .filter(~col("DRVR_LIC_CLS_ID").isin(['UNLICENSED','NA']))
            
print(question4.count())
display(question4)

3775


CRASH_ID UNIT_NBR UNIT_DESC_ID VEH_PARKED_FL VEH_HNR_FL VEH_LIC_STATE_ID VIN VEH_MOD_YEAR VEH_COLOR_ID VEH_MAKE_ID VEH_MOD_ID VEH_BODY_STYL_ID EMER_RESPNDR_FL OWNR_ZIP FIN_RESP_PROOF_ID FIN_RESP_TYPE_ID VEH_DMAG_AREA_1_ID VEH_DMAG_SCL_1_ID FORCE_DIR_1_ID VEH_DMAG_AREA_2_ID VEH_DMAG_SCL_2_ID FORCE_DIR_2_ID VEH_INVENTORIED_FL VEH_TRANSP_NAME VEH_TRANSP_DEST CONTRIB_FACTR_1_ID CONTRIB_FACTR_2_ID CONTRIB_FACTR_P1_ID VEH_TRVL_DIR_ID FIRST_HARM_EVT_INV_ID INCAP_INJRY_CNT NONINCAP_INJRY_CNT POSS_INJRY_CNT NON_INJRY_CNT UNKN_INJRY_CNT TOT_INJRY_CNT DEATH_CNT PRSN_NBR PRSN_TYPE_ID PRSN_OCCPNT_POS_ID PRSN_INJRY_SEV_ID PRSN_AGE PRSN_ETHNICITY_ID PRSN_GNDR_ID PRSN_EJCT_ID PRSN_REST_ID PRSN_AIRBAG_ID PRSN_HELMET_ID PRSN_SOL_FL PRSN_ALC_SPEC_TYPE_ID PRSN_ALC_RSLT_ID PRSN_BAC_TEST_RSLT PRSN_DRG_SPEC_TYPE_ID PRSN_DRG_RSLT_ID DRVR_DRG_CAT_1_ID PRSN_DEATH_TIME INCAP_INJRY_CNT NONINCAP_INJRY_CNT POSS_INJRY_CNT NON_INJRY_CNT UNKN_INJRY_CNT TOT_INJRY_CNT DEATH_CNT DRVR_LIC_TYPE_ID DRVR_LIC_STATE_ID DRVR_LIC_CLS_ID DRVR_ZIP 14915720 1 MOTOR VEHICLE N Y TX 1D3HV13T39S800302 NA GRY DODGE RAM 1500 PICKUP N 75407 1 PROOF OF LIABILITY INSURANCE FRONT END DAMAGE CONCENTRATED IMPACT NO DAMAGE 12 NA NA NA N null null DRIVER INATTENTION FAILED TO CONTROL SPEED NA EAST Y 0 0 0 1 0 0 0 1 DRIVER FRONT LEFT NOT INJURED 35 WHITE MALE NO SHOULDER & LAP BELT NOT DEPLOYED NOT APPLICABLE N NONE NA NA NONE NOT APPLICABLE NOT APPLICABLE null 0 0 0 1 0 0 0 DRIVER LICENSE Texas CLASS C AND M 75407 14944095 5 MOTOR VEHICLE N Y UN null NA SIL CHEVROLET CRUZE PASSENGER CAR, 4-DOOR N null 2 NA BACK END DAMAGE DISTRIBUTED IMPACT DAMAGED 1 MINIMUM 6 NA NA NA N null FSGI NONE NA NA NORTH N 0 0 0 0 1 0 0 1 DRIVER FRONT LEFT UNKNOWN NA ASIAN MALE NO UNKNOWN UNKNOWN NOT APPLICABLE N NONE NA NA NONE NOT APPLICABLE NOT APPLICABLE null 0 0 0 0 1 0 0 UNKNOWN Unknown UNKNOWN null 14922274 1 MOTOR VEHICLE N Y TX 1G11E5SA1GF139742 NA SIL CHEVROLET MALIBU PASSENGER CAR, 4-DOOR N 74134 1 PROOF OF LIABILITY INSURANCE FRONT END (RIGHT) DAMAGE PARTIAL CONTACT DAMAGED 5 1 NA NA NA N LEFT ON SCENE UNKNOWN NA NA DRIVER INATTENTION SOUTH Y 0 0 1 0 0 1 0 1 DRIVER FRONT LEFT POSSIBLE INJURY 35 WHITE FEMALE NO SHOULDER & LAP BELT NOT DEPLOYED NOT APPLICABLE N NONE NA NA NONE NOT APPLICABLE NOT APPLICABLE null 0 0 1 0 0 1 0 DRIVER LICENSE Texas CLASS C 78624 14930436 1 MOTOR VEHICLE N Y TX 19XFA1F55BE033103 NA BLK HONDA CIVIC PASSENGER CAR, 4-DOOR N 75093 1 LIABILITY INSURANCE POLICY FRONT END (LEFT) DAMAGE PARTIAL CONTACT DAMAGED 2 11 NA NA NA N LW'S 15020 KING RD, FRISCO, TX FAILED TO DRIVE IN SINGLE LANE NA NA SOUTH Y 0 0 0 0 1 0 0 1 DRIVER FRONT LEFT UNKNOWN 26 WHITE FEMALE NO UNKNOWN NOT DEPLOYED NOT APPLICABLE N NONE NA NA NONE NOT APPLICABLE NOT APPLICABLE null 0 0 0 0 1 0 0 DRIVER LICENSE Texas CLASS C 75093 14940699 1 MOTOR VEHICLE N Y TX 2MEFM74WX3X675641 2003 MAR MERCURY GRAND MARQUIS PASSENGER CAR, 4-DOOR N 75149 1 PROOF OF LIABILITY INSURANCE FRONT END DAMAGE DISTRIBUTED IMPACT DAMAGED 1 MINIMUM 12 NA NA NA Y MCINTYRE IMPOUND LOT DRIVER INATTENTION NA NA WEST Y 0 0 0 1 0 0 0 1 DRIVER FRONT LEFT NOT INJURED 21 HISPANIC FEMALE NO UNKNOWN NOT DEPLOYED NOT APPLICABLE N NONE NA NA NONE NOT APPLICABLE NOT APPLICABLE null 0 0 0 1 0 0 0 UNKNOWN Unknown UNKNOWN 75149 14941021 1 MOTOR VEHICLE N Y TX 1J4F449S44P753225 2004 SIL JEEP LIBERTY SPORT UTILITY VEHICLE N 75007 1 PROOF OF LIABILITY INSURANCE FRONT END (RIGHT) DAMAGE PARTIAL CONTACT DAMAGED 1 MINIMUM 9 NA NA NA N null null DRIVER INATTENTION NA NA SOUTH Y 0 0 0 1 0 0 0 1 DRIVER FRONT LEFT NOT INJURED 56 WHITE FEMALE NO SHOULDER & LAP BELT NOT DEPLOYED NOT APPLICABLE N NONE NA NA NONE NOT APPLICABLE NOT APPLICABLE null 0 0 0 1 0 0 0 DRIVER LICENSE Texas CLASS C 75007 14941618 2 MOTOR VEHICLE N Y UN null NA RED FORD F150 PICKUP N null NA NA DISTRIBUTED RIGHT SIDE DAMAGE PARALLEL IMPACT DAMAGED 1 MINIMUM 6 NA NA NA N null null NONE NA NA WEST Y 0 0 0 0 1 0 0 1 UNKNOWN UNKNOWN UNKNOWN NA UNKNOWN UNKNOWN NOT APPLICABLE NOT APPLICABLE NOT APPLICA

In [0]:
question5 = person_df.filter((col('PRSN_GNDR_ID') != "FEMALE") & (~col('DRVR_LIC_STATE_ID').isin(['NA','Unknown','Other'])))\
            .groupBy("DRVR_LIC_STATE_ID").count(). \
            orderBy(col("count").desc()).limit(1)\
          .select("DRVR_LIC_STATE_ID")
display(question5)
print([row[0] for row in question5.collect()])

DRVR_LIC_STATE_ID Texas

['Texas']


In [0]:
question6 = units_df.filter(col('VEH_MAKE_ID')!='NA')\
            .withColumn('INJURY_DEATH_TOTAL',col('TOT_INJRY_CNT')+col('DEATH_CNT'))\
            .groupBy('VEH_MAKE_ID').agg(sum('INJURY_DEATH_TOTAL').alias('SUM_INJURED_DEATH'))\
            .orderBy(col('SUM_INJURED_DEATH').desc())
question6 = question6.limit(5).subtract(question6.limit(2))

display(question6)
print([row[0] for row in question6.collect()])

VEH_MAKE_ID SUM_INJURED_DEATH TOYOTA 4227 DODGE 3138 NISSAN 3114

['TOYOTA', 'DODGE', 'NISSAN']


In [0]:
temp7= units_df.filter((~col('VEH_BODY_STYL_ID').isin(['NA', 'UNKNOWN', 'NOT REPORTED'])) & (~col('VEH_BODY_STYL_ID').like('OTHER%')))\
        .join(person_df.filter(~col('PRSN_ETHNICITY_ID').isin(["NA", "UNKNOWN"])),on=['CRASH_ID','UNIT_NBR'],how="inner")\
        .groupBy('VEH_BODY_STYL_ID','PRSN_ETHNICITY_ID').count()


window = Window.partitionBy('VEH_BODY_STYL_ID').orderBy(col('count').desc())
question7= temp7.withColumn("EG_RANK",dense_rank().over(window)).filter(col('EG_RANK')==1).drop('EG_RANK','count')
display(question7)

VEH_BODY_STYL_ID PRSN_ETHNICITY_ID AMBULANCE WHITE BUS BLACK FARM EQUIPMENT WHITE FIRE TRUCK WHITE MOTORCYCLE WHITE NEV-NEIGHBORHOOD ELECTRIC VEHICLE WHITE PASSENGER CAR, 2-DOOR WHITE PASSENGER CAR, 4-DOOR WHITE PICKUP WHITE POLICE CAR/TRUCK WHITE POLICE MOTORCYCLE WHITE SPORT UTILITY VEHICLE WHITE TRUCK WHITE TRUCK TRACTOR WHITE VAN WHITE YELLOW SCHOOL BUS BLACK

In [0]:
question8 = units_df.filter((col('CONTRIB_FACTR_1_ID').contains('ALCOHOL'))|(col('CONTRIB_FACTR_2_ID').contains('ALCOHOL'))|(col('CONTRIB_FACTR_P1_ID').contains    ('ALCOHOL'))|(col('CONTRIB_FACTR_1_ID').contains('DRINKING'))|(col('CONTRIB_FACTR_2_ID').contains('DRINKING'))|(col('CONTRIB_FACTR_P1_ID').contains('DRINKING')))\
            .join(person_df.dropna(subset=["DRVR_ZIP"]),on=['CRASH_ID','UNIT_NBR'],how="inner")\
            .groupBy('DRVR_ZIP').count()\
            .orderBy(col('count').desc())\
            .limit(5)\
            .select('DRVR_ZIP')
display(question8)

DRVR_ZIP count 78521 66 78130 55 76010 53 78550 51 78666 51

In [0]:
insured=charges_df.filter(col('CHARGE').contains('NO')).filter(col('CHARGE').contains('INSURANCE')).select('CRASH_ID','UNIT_NBR').distinct()
nodamage=damage_df.filter((col('DAMAGED_PROPERTY').isNull())|(col('DAMAGED_PROPERTY').contains('NONE'))).distinct().select('CRASH_ID')
# new=insured.join(nodamage,on=['CRASH_ID'],how="inner")
question9 = units_df.join(insured,on=['CRASH_ID','UNIT_NBR'],how="inner")\
            .join(nodamage,on=['CRASH_ID'],how="inner")\
            .withColumn('DMG_1_LEVEL',regexp_extract(col('VEH_DMAG_SCL_1_ID'), "\\d+", 0))\
	          .withColumn('DMG_2_LEVEL',regexp_extract(col('VEH_DMAG_SCL_2_ID'), "\\d+", 0)) \
	          .filter((col('DMG_1_LEVEL').cast('int') > 4) | (col('DMG_2_LEVEL').cast('int') > 4))
# display(new)
# display(insured)
# display(nodamage)
display(question9)

CRASH_ID UNIT_NBR UNIT_DESC_ID VEH_PARKED_FL VEH_HNR_FL VEH_LIC_STATE_ID VIN VEH_MOD_YEAR VEH_COLOR_ID VEH_MAKE_ID VEH_MOD_ID VEH_BODY_STYL_ID EMER_RESPNDR_FL OWNR_ZIP FIN_RESP_PROOF_ID FIN_RESP_TYPE_ID VEH_DMAG_AREA_1_ID VEH_DMAG_SCL_1_ID FORCE_DIR_1_ID VEH_DMAG_AREA_2_ID VEH_DMAG_SCL_2_ID FORCE_DIR_2_ID VEH_INVENTORIED_FL VEH_TRANSP_NAME VEH_TRANSP_DEST CONTRIB_FACTR_1_ID CONTRIB_FACTR_2_ID CONTRIB_FACTR_P1_ID VEH_TRVL_DIR_ID FIRST_HARM_EVT_INV_ID INCAP_INJRY_CNT NONINCAP_INJRY_CNT POSS_INJRY_CNT NON_INJRY_CNT UNKN_INJRY_CNT TOT_INJRY_CNT DEATH_CNT DMG_1_LEVEL DMG_2_LEVEL

In [0]:
top10colourdf = units_df.filter(col('VEH_COLOR_ID') != 'NA').select('VEH_COLOR_ID').groupBy('VEH_COLOR_ID').count()\
                .withColumn('RN',row_number().over(Window.orderBy(col('count').desc()))).filter("RN <=10").select('VEH_COLOR_ID')
top10States = units_df.filter(col('VEH_LIC_STATE_ID')!='NA').select('VEH_LIC_STATE_ID').groupBy('VEH_LIC_STATE_ID').count()\
                .withColumn('RN',row_number().over(Window.orderBy(col('count').desc()))).filter("RN <=25").select('VEH_LIC_STATE_ID')

question10 = charges_df.filter(col('CHARGE').contains('SPEED')).distinct()\
              .join(person_df.filter(~col("DRVR_LIC_CLS_ID").isin(['UNLICENSED','NA'])),on=['CRASH_ID','UNIT_NBR'],how="inner")\
              .join(units_df,on=['CRASH_ID','UNIT_NBR'],how="inner")\
              .join(top10colourdf,on=['VEH_COLOR_ID'],how="inner")\
              .join(top10States,on=['VEH_LIC_STATE_ID'],how="inner")\
              .groupBy('VEH_MAKE_ID').count()\
              .orderBy(col('count').desc())\
              .limit(5)
# display(top10colourdf)
display(question10)

VEH_MAKE_ID count FORD 4268 CHEVROLET 3710 TOYOTA 2274 DODGE 1914 HONDA 1391